# Big Data Project - Analyzing Patterns for Brooklyn Traffic Accidents
## Authors
* Aakash Anil Khatu ak7665
* Rutvi Jiten Bheda 

In [1]:
import pandas as pd
import sqlalchemy
import numpy as np
from itertools import product
import plotly.express as px
import plotly.io as pio
from sklearn.cluster import KMeans

In [2]:
pio.templates.default = "ggplot2"

In [3]:
# Setup SQL Alchemy for connecting to PostgresSQL
host = "localhost"
database = "ny_accidents_data"
user = "Python-Connector"
password = "Pandas"
engine = sqlalchemy.create_engine(
    f"postgresql://{user}:{password}@{host}:5432/{database}"
)
query = """
    SELECT *
    FROM accidents
    WHERE "BOROUGH" = 'BROOKLYN'
    AND CAST("YEAR" as INTEGER) BETWEEN 2019 AND 2022;
"""
# get data for brooklyn only
brooklyn_accidents = pd.read_sql(query, engine)
# clean data with missing lat and long
brooklyn_accidents = brooklyn_accidents[
    brooklyn_accidents["LATITUDE"].notna() | brooklyn_accidents["LONGITUDE"].notna()
]

## Question 2

In [4]:
accidents_2019_22 = brooklyn_accidents[
    (brooklyn_accidents["YEAR"] == "2019") | (brooklyn_accidents["YEAR"] == "2022")
]
accidents_2019_22["NUMBER OF CARS INVOLVED"] = accidents_2019_22[
    [
        "VEHICLE TYPE CODE 1",
        "VEHICLE TYPE CODE 2",
        "VEHICLE TYPE CODE 3",
        "VEHICLE TYPE CODE 4",
        "VEHICLE TYPE CODE 5",
    ]
].apply(lambda x: x.count(), axis=1)

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\1939273216.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  accidents_2019_22["NUMBER OF CARS INVOLVED"] = accidents_2019_22[


In [5]:
# Total Number of Cars Involved in Collision in each Year
px.histogram(
    accidents_2019_22[["NUMBER OF CARS INVOLVED", "YEAR"]]
    .value_counts()
    .sort_index()
    .reset_index(),
    x="YEAR",
    y="count",
    color="NUMBER OF CARS INVOLVED",
    barmode="relative",
    text_auto=True,
    height=1024,
).update_layout(
    title="Total Number of Cars Involved in Collision in each Year",
    xaxis_title="Year",
    yaxis_title="Number of Accidents",
    legend_title="Number of Cars in each collision",
    font_family="Lato",
    font_size=18,
)

In [6]:
# dumbell plot for change in pedestrian accidents
pedestrian_data = (
    accidents_2019_22[
        [
            "NUMBER OF PERSONS INJURED",
            "NUMBER OF PERSONS KILLED",
            "NUMBER OF CYCLIST INJURED",
            "NUMBER OF CYCLIST KILLED",
            "NUMBER OF PEDESTRIANS INJURED",
            "NUMBER OF PEDESTRIANS KILLED",
            "NUMBER OF MOTORIST INJURED",
            "NUMBER OF MOTORIST KILLED",
            "YEAR",
        ]
    ]
    .groupby("YEAR")
    .sum()
    .stack()
    .reset_index()
)
pedestrian_data["level_1"] = pedestrian_data["level_1"].apply(lambda x: x.title())
px.scatter(
    pedestrian_data,
    x=0,
    y="level_1",
    color="YEAR",
    size=[2 if i == "2022" else 1 for i in pedestrian_data["YEAR"]],
    text=0,
    width=2048,
).update_layout(
    title="Number of Injuries and Deaths in Each Year",
    xaxis_title="Total",
    yaxis_title="",
    legend_title="Year",
    font_family="Lato",
    font_size=18,
)

In [7]:
# Accident Density HeatMap 2019
t = accidents_2019_22
t = t[t["YEAR"] == "2019"]
t.loc[:, "LABELS"] = KMeans(n_clusters=300, random_state=0, n_init="auto").fit_predict(
    t[["LATITUDE", "LONGITUDE"]]
)
t.loc[:, "COLOR"] = t["LABELS"].map(t.LABELS.value_counts().to_dict())
px.scatter_mapbox(
    t,
    lat="LATITUDE",
    lon="LONGITUDE",
    color="COLOR",
    mapbox_style="open-street-map",
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
    color_continuous_scale="deep",
).update_traces(marker={"size": 10}).update_layout(
    title="Accident Density HeatMap 2019",
    coloraxis_colorbar_title_text="Number of Accidents",
    font_size=18,
)

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\3978663568.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\3978663568.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [9]:
t = accidents_2019_22
t = t[t["YEAR"] == "2019"]
t.loc[:, "LABELS"] = KMeans(n_clusters=300, random_state=0, n_init="auto").fit_predict(
    t[["LATITUDE", "LONGITUDE"]]
)
t.loc[:, "COLOR"] = t["LABELS"].map(t.LABELS.value_counts().to_dict())
px.scatter_mapbox(
    t,
    lat="LATITUDE",
    lon="LONGITUDE",
    color="COLOR",
    mapbox_style="open-street-map",
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
    color_continuous_scale="deep",
).update_traces(marker={"size": 10}).update_layout(
    title="Accident Density HeatMap 2022",
    coloraxis_colorbar_title_text="Number of Accidents",
    font_size=18,
)

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\3476644402.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\3476644402.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [10]:
t = accidents_2019_22
t = t[t["YEAR"] == "2019"]
px.density_mapbox(
    t,
    lat="LATITUDE",
    lon="LONGITUDE",
    radius=15,
    mapbox_style="open-street-map",
    range_color=[1, 20],
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
)

## Question 3

In [11]:
june_2020_accidents = brooklyn_accidents[
    (brooklyn_accidents["MONTH"] == "06") & (brooklyn_accidents["YEAR"] == "2020")
]
june_2022_accidents = brooklyn_accidents[
    (brooklyn_accidents["MONTH"] == "06") & (brooklyn_accidents["YEAR"] == "2022")
]
june_accidents = brooklyn_accidents[
    (brooklyn_accidents["MONTH"] == "06")
    & ((brooklyn_accidents["YEAR"] == "2020") | (brooklyn_accidents["YEAR"] == "2022"))
]

In [12]:
px.density_mapbox(
    june_2020_accidents,
    lat="LATITUDE",
    lon="LONGITUDE",
    radius=15,
    mapbox_style="open-street-map",
    range_color=[1, 4],
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
)

In [13]:
Sum_of_squared_distances = []
K = range(5, 300)
for k in K:
    km = KMeans(n_clusters=k, random_state=0, n_init="auto")
    km = km.fit(brooklyn_accidents[["LATITUDE", "LONGITUDE"]])
    Sum_of_squared_distances.append(km.inertia_)

In [14]:
px.line(x=K, y=Sum_of_squared_distances).update_traces(
    marker={"size": 20}
).update_layout(
    title="Kmeans Ideal Number of Clusters",
    xaxis_title="Number of Clusters",
    yaxis_title="SSE",
    font_size=18,
)

In [15]:
june_2020_accidents.loc[:, "LABELS"] = KMeans(
    n_clusters=300, random_state=0, n_init="auto"
).fit_predict(june_2020_accidents[["LATITUDE", "LONGITUDE"]])
june_2020_accidents.loc[:, "COLOR"] = june_2020_accidents["LABELS"].map(
    june_2020_accidents.LABELS.value_counts().to_dict()
)
px.scatter_mapbox(
    june_2020_accidents,
    lat="LATITUDE",
    lon="LONGITUDE",
    color="COLOR",
    mapbox_style="open-street-map",
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
    color_continuous_scale="deep",
).update_traces(marker={"size": 20}).update_layout(
    title="Accident Density HeatMap June 2020",
    coloraxis_colorbar_title_text="Number of Accidents",
    font_size=18,
)

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\2730210087.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\2730210087.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [16]:
june_2022_accidents.loc[:, "LABELS"] = KMeans(
    n_clusters=300, random_state=0, n_init="auto"
).fit_predict(june_2022_accidents[["LATITUDE", "LONGITUDE"]])
june_2022_accidents.loc[:, "COLOR"] = june_2022_accidents["LABELS"].map(
    june_2022_accidents.LABELS.value_counts().to_dict()
)
px.scatter_mapbox(
    june_2022_accidents,
    lat="LATITUDE",
    lon="LONGITUDE",
    color="COLOR",
    mapbox_style="open-street-map",
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
    color_continuous_scale="deep",
).update_traces(marker={"size": 20}).update_layout(
    title="Accident Density HeatMap June 2022",
    coloraxis_colorbar_title_text="Number of Accidents",
    font_size=18,
)

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\3004716252.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\3004716252.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [17]:
# dumbell plot for change in pedestrian accidents
pedestrian_data = (
    june_accidents[
        [
            "NUMBER OF PERSONS INJURED",
            "NUMBER OF PERSONS KILLED",
            "NUMBER OF CYCLIST INJURED",
            "NUMBER OF CYCLIST KILLED",
            "NUMBER OF PEDESTRIANS INJURED",
            "NUMBER OF PEDESTRIANS KILLED",
            "NUMBER OF MOTORIST INJURED",
            "NUMBER OF MOTORIST KILLED",
            "YEAR",
        ]
    ]
    .groupby("YEAR")
    .sum()
    .stack()
    .reset_index()
)
pedestrian_data["level_1"] = pedestrian_data["level_1"].apply(lambda x: x.title())
px.scatter(
    pedestrian_data,
    x=0,
    y="level_1",
    color="YEAR",
    size=[1 if i == "2020" else 2 for i in pedestrian_data["YEAR"]],
    width=2048,
).update_layout(
    title="Number of Injuries and Deaths in June of 2020 and 2022",
    xaxis_title="Total",
    yaxis_title="",
    legend_title="Year",
    font_family="Lato",
    font_size=18,
)

In [18]:
vehicle_type_df = june_accidents[
    [
        "VEHICLE TYPE CODE 1",
        "VEHICLE TYPE CODE 2",
        "VEHICLE TYPE CODE 3",
        "VEHICLE TYPE CODE 4",
        "VEHICLE TYPE CODE 5",
        "YEAR",
    ]
]
vehicle_type_df["combined"] = vehicle_type_df[
    [
        "VEHICLE TYPE CODE 1",
        "VEHICLE TYPE CODE 2",
        "VEHICLE TYPE CODE 3",
        "VEHICLE TYPE CODE 4",
        "VEHICLE TYPE CODE 5",
    ]
].values.tolist()
vehicle_type_df.explode("combined")[["YEAR", "combined"]].value_counts().reset_index()

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\184487065.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



YEAR                             combined  count
0    2022                                Sedan   1635
1    2020                                Sedan   1427
2    2022  Station Wagon/Sport Utility Vehicle   1213
3    2020  Station Wagon/Sport Utility Vehicle   1100
4    2022                                 Bike    162
..    ...                                  ...    ...
107  2020                            Open Body      1
108  2020                           NYC AMBULA      1
109  2020                            Motorbike      1
110  2020                             Minibike      1
111  2020                                  UNK      1

[112 rows x 3 columns]

In [19]:
px.bar(
    vehicle_type_df.explode("combined")[["YEAR", "combined"]]
    .value_counts()
    .reset_index(),
    y="count",
    x="combined",
    color="YEAR",
    barmode="group",
    log_y=True,
    height=1024,
    width=2048,
    text_auto="s",
).update_layout(
    title="Reported Type of Vehicles in Accidents in June 2020 and June 2022",
    xaxis_title="Contributing Cause",
    yaxis_title="Number of Accidents (Log Scale)",
    legend_title="Year",
    font_family="Lato",
    font_size=18,
).update_xaxes(
    tickangle=45
)

## Question 4

In [20]:
july_accidents = brooklyn_accidents[
    (brooklyn_accidents["MONTH"] == "07")
    & ((brooklyn_accidents["YEAR"] == "2020") | (brooklyn_accidents["YEAR"] == "2022"))
]
contributing_factor_df = july_accidents[
    [
        "CONTRIBUTING FACTOR VEHICLE 1",
        "CONTRIBUTING FACTOR VEHICLE 2",
        "CONTRIBUTING FACTOR VEHICLE 3",
        "CONTRIBUTING FACTOR VEHICLE 4",
        "CONTRIBUTING FACTOR VEHICLE 5",
        "YEAR",
    ]
]
contributing_factor_df["combined"] = contributing_factor_df[
    [
        "CONTRIBUTING FACTOR VEHICLE 1",
        "CONTRIBUTING FACTOR VEHICLE 2",
        "CONTRIBUTING FACTOR VEHICLE 3",
        "CONTRIBUTING FACTOR VEHICLE 4",
        "CONTRIBUTING FACTOR VEHICLE 5",
    ]
].values.tolist()
contributing_factor_df.explode("combined")[
    ["YEAR", "combined"]
].value_counts().reset_index()

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\4009418584.py:15: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



YEAR                        combined  count
0   2020  Driver Inattention/Distraction    609
1   2022  Driver Inattention/Distraction    592
2   2020   Failure to Yield Right-of-Way    157
3   2022   Failure to Yield Right-of-Way    129
4   2020           Following Too Closely     91
..   ...                             ...    ...
68  2020         Prescription Medication      1
69  2020      Driverless/Runaway Vehicle      1
70  2020          Cell Phone (hand-Held)      1
71  2020    Shoulders Defective/Improper      1
72  2020           Accelerator Defective      1

[73 rows x 3 columns]

In [21]:
px.bar(
    contributing_factor_df.explode("combined")[["YEAR", "combined"]]
    .value_counts()
    .reset_index(),
    y="count",
    x="combined",
    color="YEAR",
    barmode="group",
    log_y=True,
    height=1024,
    width=2048,
    text_auto="s",
).update_layout(
    title="Contributing Causes of Accidents in July 2020 and July 2022",
    xaxis_title="Contributing Cause",
    yaxis_title="Number of Reports",
    legend_title="Year",
    font_family="Lato",
    font_size=18,
).update_xaxes(
    tickangle=45
)

In [22]:
t = july_accidents
t = t[t["YEAR"] == "2020"]
t.loc[:, "LABELS"] = KMeans(n_clusters=300, random_state=0, n_init="auto").fit_predict(
    t[["LATITUDE", "LONGITUDE"]]
)
t.loc[:, "COLOR"] = t["LABELS"].map(t.LABELS.value_counts().to_dict())
px.scatter_mapbox(
    t,
    lat="LATITUDE",
    lon="LONGITUDE",
    color="COLOR",
    mapbox_style="open-street-map",
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
    color_continuous_scale="deep",
).update_traces(marker={"size": 20}).update_layout(
    title="Accident Density HeatMap July 2020",
    coloraxis_colorbar_title_text="Number of Accidents",
    font_size=18,
)

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\294757459.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\294757459.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [23]:
t = july_accidents
t = t[t["YEAR"] == "2022"]
t.loc[:, "LABELS"] = KMeans(n_clusters=300, random_state=0, n_init="auto").fit_predict(
    t[["LATITUDE", "LONGITUDE"]]
)
t.loc[:, "COLOR"] = t["LABELS"].map(t.LABELS.value_counts().to_dict())
px.scatter_mapbox(
    t,
    lat="LATITUDE",
    lon="LONGITUDE",
    color="COLOR",
    mapbox_style="open-street-map",
    width=1024,
    height=1024,
    zoom=11.4,
    center={"lat": 40.654, "lon": -73.94958},
    color_continuous_scale="deep",
).update_traces(marker={"size": 20}).update_layout(
    title="Accident Density HeatMap July 2022",
    coloraxis_colorbar_title_text="Number of Accidents",
    font_size=18,
)

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\1447374452.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\aakas\AppData\Local\Temp\ipykernel_27064\1447374452.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Question 5

In [24]:
px.line(
    brooklyn_accidents["CRASH DATE"]
    .groupby(brooklyn_accidents["CRASH DATE"])
    .count()
    .rolling(60)
    .sum()
    .dropna(),
    width=2048,
    height=1024,
).update_layout(
    title="Total Accidents in 60 Consecuitive Days ",
    xaxis_title="Date",
    yaxis_title="Total Number of Accidents in previous 60 Days",
    font_family="Lato",
    font_size=18,
    showlegend=False,
).update_xaxes(
    tickangle=45
)

In [25]:
consecuitive_accidents_df = (
    brooklyn_accidents["CRASH DATE"]
    .groupby(brooklyn_accidents["CRASH DATE"])
    .count()
    .rolling(60)
    .sum()
    .dropna()
)
consecuitive_accidents_df[
    (consecuitive_accidents_df.index >= "2020-03-01")
    & (consecuitive_accidents_df.index < "2022-10-01")
].sort_values(ascending=False)

Series([], Name: CRASH DATE, dtype: float64)

## Question 6

In [26]:
from pandas.api.types import CategoricalDtype
brooklyn_accidents["CRASH DATE"] = pd.to_datetime(brooklyn_accidents["CRASH DATE"])
brooklyn_accidents["DAY OF WEEK"] = brooklyn_accidents["CRASH DATE"].dt.day_name()
day_categories = [
    "Monday",
    "Tuesday",
    "Wednesday",
    "Thursday",
    "Friday",
    "Saturday",
    "Sunday",
]
cat_type = CategoricalDtype(categories=day_categories, ordered=True)
brooklyn_accidents["DAY OF WEEK"] = brooklyn_accidents["DAY OF WEEK"].astype(cat_type)
accidents_by_day = (
    brooklyn_accidents.groupby("DAY OF WEEK", observed=False)
    .size()
    .reset_index(name="accident_count")
)

In [27]:
fig = px.bar(accidents_by_day, y="DAY OF WEEK", x="accident_count", text_auto=True)
fig.update_layout(yaxis=dict(autorange="reversed"))
fig.update_layout(
    title="Number Of Accidents by Day of the Week 2019-2022",
    xaxis_title="Number of Accidents",
    yaxis_title="Day Of the Week",
    legend_title="Legend Title",
)

## Question 8

In [28]:
acc_6_to_12 = pd.to_datetime(brooklyn_accidents["CRASH TIME"], format="%H:%M")
acc_6_to_12 = acc_6_to_12[(acc_6_to_12.dt.hour >= 6) & (acc_6_to_12.dt.hour <= 12)]
acc_by_hour = acc_6_to_12.groupby(acc_6_to_12.dt.hour).size().reset_index(name="count")

In [29]:
fig = px.bar(acc_by_hour, y="count", x="CRASH TIME", text_auto=True)
fig.update_layout(
    title="Accidents in Hour of the Day",
    xaxis_title="Hour (24h Format)",
    yaxis_title="Number of Accidents",
    legend_title="Legend Title",
)

## Question 10

In [30]:
px.bar(
    brooklyn_accidents["CRASH DATE"].value_counts().sort_index(), width=2048
).update_layout(
    title="Total Accidents on Each Day ",
    xaxis_title="Date",
    yaxis_title="Total Number of Accidents",
    font_family="Lato",
    font_size=18,
)

c:\Users\aakas\AppData\Local\Programs\Python\Python311\Lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [31]:
brooklyn_accidents.loc[
    brooklyn_accidents["YEAR"] == "2022", "CRASH DATE"
].value_counts().sort_values(ascending=False)[:10]

CRASH DATE
2022-12-16    99
2022-11-02    92
2022-09-06    91
2022-05-31    91
2022-08-08    88
2022-09-16    88
2022-09-09    88
2022-06-17    88
2022-06-10    88
2022-03-25    87
Name: count, dtype: int64